In [1]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
 
# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
 
# Enable logging for gensim - optional
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
 
# Plotting tools
import pyLDAvis
import pyLDAvis.gensim # don't skip this
import matplotlib.pyplot as plt
%matplotlib inline
    
import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

# 토큰으로 분리된 단어들 중 명사만 추출

In [2]:
# 명사 파일 로드

data=pd.read_excel('C:\\Users\\user\\Desktop\\기타\\data_pos_nva.xlsx')

In [3]:
# 컬럼확인

data.columns

Index(['c_n_pos_a', 'c_n_pos_v', 'c_n_pos_n_more1', 'c_n_pos_n_more2',
       't_n_pos_a', 't_n_pos_v'],
      dtype='object')

In [4]:
# 빈도 수 2개 이하는 제거한 명사만 추출

data_n=data['c_n_pos_n_more2']

In [5]:
# 결측치 제거

data_n=data_n.dropna(axis=0)

In [6]:
# 확인

data_n

0          반도체
1           전자
2           기업
3           시장
4           사업
5           기술
6           삼성
7           투자
8           산업
9           중국
10          수출
11          업체
12          실적
13          개발
14          증가
15          한국
16          생산
17          이익
18          영업
19         지난해
20          제품
21          매출
22          세계
23          올해
24          전망
25          미국
26          대비
27          기록
28          성장
29          지난
         ...  
46211       싹둑
46212      길병송
46213       티민
46214       넥타
46215       북후
46216      임영환
46217      브레트
46218      공단로
46219     애브비사
46220       압델
46221    페르시아만
46222       민항
46223       팔콘
46224     어댑티드
46225       등방
46226      렌틸콩
46227       방물
46228     트리스탄
46229     게임스톱
46230      뒷구멍
46231      이훈구
46232      박덕진
46233      정수현
46234       라덴
46235     덕영대로
46236      중재위
46237       광초
46238      사할린
46239     간접흡연
46240       필순
Name: c_n_pos_n_more2, Length: 46241, dtype: object

In [7]:
# 리스트로 변환

data_nl=data_n.tolist()

In [8]:
# 확인

data_nl

['반도체',
 '전자',
 '기업',
 '시장',
 '사업',
 '기술',
 '삼성',
 '투자',
 '산업',
 '중국',
 '수출',
 '업체',
 '실적',
 '개발',
 '증가',
 '한국',
 '생산',
 '이익',
 '영업',
 '지난해',
 '제품',
 '매출',
 '세계',
 '올해',
 '전망',
 '미국',
 '대비',
 '기록',
 '성장',
 '지난',
 '국내',
 '감소',
 '분야',
 '증권',
 '규모',
 '하락',
 '부문',
 '상승',
 '대한',
 '그룹',
 '자동차',
 '최근',
 '통해',
 '확대',
 '위해',
 '때문',
 '디스플레이',
 '관련',
 '예상',
 '글로벌',
 '회사',
 '주가',
 '장비',
 '스마트폰',
 '이번',
 '이후',
 '계획',
 '정부',
 '개선',
 '경제',
 '공장',
 '회장',
 '현재',
 '이상',
 '연구원',
 '대표',
 '발표',
 '하이닉스',
 '업종',
 '수준',
 '지원',
 '업계',
 '최대',
 '부품',
 '분석',
 '가격',
 '시스템',
 '기자',
 '공급',
 '전략',
 '수요',
 '대해',
 '경우',
 '종목',
 '바이오',
 '예정',
 '일본',
 '설명',
 '판매',
 '상황',
 '단지',
 '가장',
 '인수',
 '달러',
 '기준',
 '지수',
 '공정',
 '우리',
 '거래',
 '지속',
 '메모리',
 '지역',
 '서비스',
 '라며',
 '경쟁력',
 '모바일',
 '갤럭시',
 '목표',
 '협력',
 '영향',
 '미래',
 '평가',
 '매수',
 '사장',
 '관계자',
 '기존',
 '서울',
 '전체',
 '각각',
 '건설',
 '평택',
 '진행',
 '유지',
 '중심',
 '소재',
 '해외',
 '연구',
 '시작',
 '혁신',
 '효과',
 '센터',
 '가능성',
 '문제',
 '주요',
 '사용',
 '나노',
 '확보',
 '경기',
 '경쟁',
 '의견',

In [17]:
# 뉴스 파일 로드

data_all=pd.read_excel('C:\\Users\\user\\Desktop\\기타\\online_news_nosw.xlsx')

In [18]:
data_all['Index']

0        198930
1        198929
2        198928
3        198926
4        198927
5        198925
6        198923
7        198924
8        198922
9        198917
10       198918
11       198919
12       198920
13       198921
14       198914
15       198915
16       198916
17       198913
18       198911
19       198912
20       198909
21       198910
22       198907
23       198908
24       198906
25       198905
26       198903
27       198904
28       198902
29       198901
          ...  
86352    112578
86353    112577
86354    112576
86355    112575
86356    112574
86357    112573
86358    112572
86359    112571
86360    112570
86361    112569
86362    112568
86363    112567
86364    112564
86365    112565
86366    112566
86367    112563
86368    112562
86369    112560
86370    112561
86371    112558
86372    112559
86373    112557
86374    112556
86375    112555
86376    112554
86377    112553
86378    112552
86379    112551
86380    112550
86381    112549
Name: Index, Length: 863

In [19]:
data_all.columns

Index(['Index', 'content', 'created_date', 'publisher', 'section', 'title',
       '분기', '실질GDP', 'pos_c', 'pos_t', 'c_n_pos'],
      dtype='object')

In [20]:
data_all['c_n_pos'][1]

"['냈다', '개발', '업계', '이를', '설계', '보인다', '연구개발', '있을', '위용', '팹리스', '잡았던', '투자', '설비', '이뤄져', '라면', '과학기술원', '비메', '나노미터', '왔다', '퀄컴', '했다', '따른', '착공', '느냐가', '넘어', '없을', '상향', '솟아', '새해', '시스템', '생산', '넘을', '않다', '키워야', '애플', '엑시노스', '나선', '치를', '신규', '빠졌다', '대표', '이익', '어려울', '사례', '빠졌던', '완공', '예측', '우세하다', '적용', '증권', '있는', '개선', '부착', '보이', '높아질', '하는', '기술', '전자기기', '전반', '확보', '없어', '처음', '앞선', '축구장', '인쇄공', '핀펫', '반도체', '과언', '아니다', '전략', '조용히', '부진', '늘리고', '신제품', '양산', '경기', '수십', '외부', '증설', '따르면', '넘는', '만드는', '않는', '수정', '나온다', '되찾아', '브랜드', '쉽지', '성장할', '조짐', '극심한', '수익', '후반', '된다', '주력', '연간', '확대', '좁혀', '실적', '일부', '전기', '적극', '분석', '차지', '쌓는', '보고', '달러', '불과하다', '규모', '본격', '국내외', '산업', '하지', '후발', '점유', '부진했던', '아니라', '격차', '높인', '역량', '차례', '탑재', '센서', '예정', '침체', '추격', '메모리', '가장', '시안', '압도', '덕분', '격화', '주자', '모바일', '추가', '상징', '유회', '출판', '되면', '내다봤다', '사업', '건설', '큼지막한', '전망', '로고', '계속', '밀려', '명운', '독식', '공정', '육박', '하락', '이어', '거래', '호황', '노릇', '고속도로', '전력'

In [21]:
# n_pos_t 리스트안의 문자형 분리 & 특수문자 제거

data_sp=[]
for i in range(len(data_all)):
    data_sp.append(data_all['c_n_pos'][i].split(','))
    
data_sp[0]

["['대한'",
 " '보인다'",
 " '올리며'",
 " '투자'",
 " '지를'",
 " '보다'",
 " '했다'",
 " '상향'",
 " '새해'",
 " '쳐졌다'",
 " '때문'",
 " '비중'",
 " '바뀌는'",
 " '이익'",
 " '넘긴'",
 " '예측'",
 " '증권'",
 " '종합'",
 " '있는'",
 " '넘길'",
 " '갔다'",
 " '성장'",
 " '하는'",
 " '국내'",
 " '반도체'",
 " '전자상거래'",
 " '이유'",
 " '따르면'",
 " '매출'",
 " '조정'",
 " '뉴스'",
 " '서다'",
 " '성장할'",
 " '된다'",
 " '연간'",
 " '확대'",
 " '맞을'",
 " '종목'",
 " '앞서'",
 " '분석'",
 " '차지'",
 " '정보'",
 " '모바일'",
 " '같은'",
 " '성장한'",
 " '포인트'",
 " '되면'",
 " '기조'",
 " '전망'",
 " '치가'",
 " '떨어질'",
 " '신선한'",
 " '이어'",
 " '나왔다'",
 " '호황'",
 " '됐다'",
 " '훌쩍'",
 " '보이는데도'",
 " '수요'",
 " '쳐지고'",
 " '시장'",
 " '최대'",
 " '전체'",
 " '영업'",
 " '재다'",
 " '걸까'",
 " '판매'",
 " '체인지'",
 " '기업'",
 " '단가'",
 " '크게'",
 " '이었던'",
 " '대비'",
 " '세계'",
 " '부문'",
 " '사이트'",
 " '역성'",
 " '겪은'",
 " '있기'",
 " '기를'",
 " '신문'",
 " '맛있는']"]

In [22]:
data_st=[]
for i in range(len(data_sp)):
    data_st2=[]
    for j in data_sp[i]:
        data_st2.append(j.lstrip('[').rstrip('"]').strip(" ' "))
    data_st.append(data_st2)

data_st[0][1]

'보인다'

In [23]:
# data_nl을 세트로 변환

a=set(data_nl)

In [24]:
# 명사파일로 필터링하여 n_pos_c 컬럼의 명사만 추출

SW_del=[]
for i in data_st:
    b=set(i)
    SW_del.append(b&a)

In [25]:
# 확인

SW_del

[{'국내',
  '기업',
  '기조',
  '뉴스',
  '단가',
  '대비',
  '대한',
  '때문',
  '매출',
  '모바일',
  '반도체',
  '부문',
  '분석',
  '비중',
  '사이트',
  '상향',
  '새해',
  '성장',
  '세계',
  '수요',
  '시장',
  '신문',
  '앞서',
  '역성',
  '연간',
  '영업',
  '예측',
  '이유',
  '이익',
  '전망',
  '전자상거래',
  '전체',
  '정보',
  '조정',
  '종목',
  '종합',
  '증권',
  '차지',
  '체인지',
  '최대',
  '치가',
  '크게',
  '투자',
  '판매',
  '포인트',
  '호황',
  '확대',
  '훌쩍'},
 {'가격',
  '가까이',
  '가장',
  '개발',
  '개선',
  '거래',
  '건설',
  '격차',
  '격화',
  '경기',
  '경쟁',
  '계속',
  '계획',
  '고속도로',
  '공략',
  '공장',
  '공정',
  '과언',
  '과학기술원',
  '관계자',
  '구매',
  '국내외',
  '규모',
  '기술',
  '기업',
  '나노미터',
  '나선',
  '노릇',
  '달러',
  '당분간',
  '대박',
  '대비',
  '대표',
  '덕분',
  '독식',
  '라면',
  '로고',
  '메모리',
  '명운',
  '모바일',
  '물량',
  '미세',
  '반도체',
  '보고',
  '보이',
  '본격',
  '부진',
  '부착',
  '분석',
  '분야',
  '브랜드',
  '비메',
  '사례',
  '사상',
  '사업',
  '사이트',
  '산업',
  '상징',
  '상향',
  '새해',
  '생산',
  '선두',
  '설계',
  '설비',
  '세계',
  '센서',
  '수십',
  '수익',
  '수정',
  '수주',
  '수준',
  '수출',
  '스마트폰',
  '시스

In [26]:
# set을 리스트로 변환

SW_del2=[]
for i in SW_del:
    SW_del2.append(list(i))

In [27]:
SW_del2[55000]

['측면',
 '계속',
 '압도',
 '수요',
 '독보',
 '달러',
 '뇌수술',
 '경영',
 '제품',
 '자동차',
 '제시',
 '고객',
 '추가',
 '가시',
 '여개',
 '대비',
 '예상',
 '불량품',
 '머니투데이',
 '자본',
 '여력',
 '전장',
 '실적',
 '출하',
 '안정',
 '전망',
 '불구',
 '전세계',
 '투자',
 '이익',
 '중이',
 '포인트',
 '최초',
 '자동',
 '보고서',
 '세계',
 '대해',
 '장비',
 '상태',
 '시장점유율',
 '기대',
 '납품',
 '기업',
 '광학',
 '단가',
 '기준',
 '차입',
 '강소기업',
 '위해',
 '통해',
 '영업',
 '개발',
 '주가',
 '고가',
 '영향',
 '상승',
 '동사',
 '차지',
 '베스트',
 '증권',
 '개시',
 '시장',
 '규모',
 '물량',
 '성장',
 '검사',
 '내비게이션',
 '기능',
 '하이엔드',
 '증가',
 '성과',
 '반도체',
 '의미',
 '현금',
 '초도',
 '목표',
 '기술',
 '사업',
 '주력',
 '매수',
 '내용',
 '연간',
 '의견',
 '신뢰',
 '경쟁',
 '로서',
 '감소',
 '확대',
 '바탕',
 '부가',
 '겸비',
 '선정',
 '금융투자',
 '반영',
 '의료',
 '판매',
 '커버',
 '공정',
 '매출',
 '경우',
 '요약',
 '고영은',
 '평가',
 '글로벌',
 '지속',
 '리포트',
 '추진']

# LDA Modeling

In [28]:
# 사전 생성

id2word = corpora.Dictionary(SW_del2)

In [29]:
# 말뭉치 생성

texts = SW_del2

In [30]:
# Term Document Frequency

corpus = [id2word.doc2bow(text) for text in texts]

In [31]:
# 확인
print(corpus[0])

[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1)]


In [32]:
# 빈도수 표시

[[(id2word[id], freq) for id, freq in cp] for cp in corpus]

[[('국내', 1),
  ('기업', 1),
  ('기조', 1),
  ('뉴스', 1),
  ('단가', 1),
  ('대비', 1),
  ('대한', 1),
  ('때문', 1),
  ('매출', 1),
  ('모바일', 1),
  ('반도체', 1),
  ('부문', 1),
  ('분석', 1),
  ('비중', 1),
  ('사이트', 1),
  ('상향', 1),
  ('새해', 1),
  ('성장', 1),
  ('세계', 1),
  ('수요', 1),
  ('시장', 1),
  ('신문', 1),
  ('앞서', 1),
  ('역성', 1),
  ('연간', 1),
  ('영업', 1),
  ('예측', 1),
  ('이유', 1),
  ('이익', 1),
  ('전망', 1),
  ('전자상거래', 1),
  ('전체', 1),
  ('정보', 1),
  ('조정', 1),
  ('종목', 1),
  ('종합', 1),
  ('증권', 1),
  ('차지', 1),
  ('체인지', 1),
  ('최대', 1),
  ('치가', 1),
  ('크게', 1),
  ('투자', 1),
  ('판매', 1),
  ('포인트', 1),
  ('호황', 1),
  ('확대', 1),
  ('훌쩍', 1)],
 [('기업', 1),
  ('대비', 1),
  ('모바일', 1),
  ('반도체', 1),
  ('분석', 1),
  ('사이트', 1),
  ('상향', 1),
  ('새해', 1),
  ('세계', 1),
  ('시장', 1),
  ('연간', 1),
  ('영업', 1),
  ('예측', 1),
  ('이익', 1),
  ('전망', 1),
  ('증권', 1),
  ('차지', 1),
  ('체인지', 1),
  ('최대', 1),
  ('투자', 1),
  ('호황', 1),
  ('확대', 1),
  ('가격', 1),
  ('가까이', 1),
  ('가장', 1),
  ('개발', 1),
  ('개선', 1),
  ('거래', 1)

In [33]:
# LDA 모델 생성

lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                            id2word=id2word,
                                            num_topics=20,
                                            random_state=100,
                                            update_every=1,
                                            chunksize=100,
                                            passes=10,
                                            alpha='auto',
                                            per_word_topics=True)

In [34]:
# 토픽 출력

pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0,
  '0.030*"지수" + 0.026*"업종" + 0.025*"거래" + 0.025*"오른" + 0.024*"상승" + 0.022*"하락" '
  '+ 0.019*"강세" + 0.019*"포인트" + 0.018*"마감" + 0.018*"증시"'),
 (1,
  '0.036*"서비스" + 0.034*"사물인터넷" + 0.034*"지능" + 0.030*"통신" + 0.030*"스마트" + '
  '0.024*"시스템" + 0.024*"제공" + 0.023*"기기" + 0.023*"플랫폼" + 0.023*"자동차"'),
 (2,
  '0.030*"우려" + 0.026*"노트" + 0.022*"가능성" + 0.019*"불확실" + 0.018*"상황" + '
  '0.017*"정책" + 0.016*"금리" + 0.015*"부담" + 0.015*"경기" + 0.014*"주의"'),
 (3,
  '0.129*"계약" + 0.113*"체결" + 0.079*"장비" + 0.069*"공급" + 0.066*"제조" + 0.060*"규모" '
  '+ 0.060*"재료" + 0.057*"반도체" + 0.045*"매출" + 0.040*"변경"'),
 (4,
  '0.019*"산업" + 0.018*"기술" + 0.018*"위해" + 0.017*"기업" + 0.017*"분야" + '
  '0.015*"반도체" + 0.015*"지원" + 0.015*"미래" + 0.014*"통해" + 0.014*"사업"'),
 (5,
  '0.098*"프로그램" + 0.089*"과학" + 0.087*"표준" + 0.084*"신뢰" + 0.057*"기여" + '
  '0.056*"합동" + 0.053*"근거" + 0.048*"과학기술" + 0.046*"규명" + 0.041*"미래창조과학부"'),
 (6,
  '0.127*"일자리" + 0.101*"특수" + 0.081*"정기" + 0.052*"개혁" + 0.050*"필요성" + '
  '0.049*"최대한" + 0.042*"행위" + 0.042*"

# 시각화

In [35]:
# Visualize the topics

pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
vis

C:\Users\user\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
8     -0.203257 -0.056184       1        1  16.428474
4     -0.201711  0.131293       2        1  13.055287
14    -0.194546 -0.012923       3        1  12.168876
9     -0.109163  0.183437       4        1   9.953220
13    -0.135682  0.096772       5        1   9.131928
16    -0.143083  0.186355       6        1   7.827806
12    -0.119110  0.022134       7        1   7.104920
2     -0.046140 -0.018771       8        1   4.277554
0     -0.080743 -0.185069       9        1   4.155849
1      0.026913  0.085429      10        1   3.600679
15    -0.116148 -0.258120      11        1   2.490285
7     -0.010320 -0.199280      12        1   2.071802
11     0.126663  0.053000      13        1   1.917002
18     0.126660  0.091341      14        1   1.247953
19     0.070566 -0.175978      15        1   1.073954
17     0.185249  0.145057      16        1   1.031023
3      0.053116 -0.073128      17        1   0.961958
5      0.255971  0.001835      18        1   0.607466
6      0.253331 -0.004392      19        1   0.533948
10     0.261432 -0.012808      20        1   0.360010, topic_info=     Category           Freq   Term          Total  loglift  logprob
10    Default  106013.000000    반도체  106013.000000  30.0000  30.0000
70    Default   32698.000000     규모   32698.000000  29.0000  29.0000
886   Default   22757.000000     공급   22757.000000  28.0000  28.0000
100   Default   34297.000000     생산   34297.000000  27.0000  27.0000
388   Default   20898.000000     장비   20898.000000  26.0000  26.0000
8     Default   19407.000000     매출   19407.000000  25.0000  25.0000
98    Default   42285.000000     산업   42285.000000  24.0000  24.0000
284   Default   28118.000000     증가   28118.000000  23.0000  23.0000
20    Default   50991.000000     시장   50991.000000  22.0000  22.0000
11    Default   20458.000000     부문   20458.000000  21.0000  21.0000
1760  Default   13027.000000     계약   13027.000000  20.0000  20.0000
146   Default   15940.000000     제조   15940.000000  19.0000  19.0000
219   Default   37963.000000     미국   37963.000000  18.0000  18.0000
110   Default   17279.000000     수출   17279.000000  17.0000  17.0000
151   Default   32001.000000     중국   32001.000000  16.0000  16.0000
71    Default   45681.000000     기술   45681.000000  15.0000  15.0000
5     Default   28883.000000     대비   28883.000000  14.0000  14.0000
42    Default   46408.000000     투자   46408.000000  13.0000  13.0000
471   Default   22104.000000     정부   22104.000000  12.0000  12.0000
359   Default   24968.000000     상승   24968.000000  11.0000  11.0000
749   Default   10412.000000     사장   10412.000000  10.0000  10.0000
1     Default   47130.000000     기업   47130.000000   9.0000   9.0000
274   Default   22375.000000    자동차   22375.000000   8.0000   8.0000
121   Default   23801.000000     업계   23801.000000   7.0000   7.0000
392   Default   29772.000000     제품   29772.000000   6.0000   6.0000
1133  Default   15156.000000     기간   15156.000000   5.0000   5.0000
539   Default   17689.000000     사용   17689.000000   4.0000   4.0000
54    Default   16657.000000     건설   16657.000000   3.0000   3.0000
500   Default   15306.000000     감소   15306.000000   2.0000   2.0000
51    Default   34225.000000     개발   34225.000000   1.0000   1.0000
...       ...            ...    ...            ...      ...      ...
2579  Topic20    4332.464844     대체    4333.657715   5.6265  -1.9130
1631  Topic20    2263.838135     단일    2265.031006   5.6263  -2.5621
1762  Topic20    2038.580078     광학    2039.773071   5.6262  -2.6669
2576  Topic20    1865.099731     광장    1866.292725   5.6262  -2.7558
914   Topic20    1695.237183   저장장치    1696.430176   5.6261  -2.8513
1480  Topic20    1450.412476  전기자동차    1451.605469   5.6260  -3.0073
2602  Topic20    1400.783325  하드디스크    1401.976318   5.6259  -3.0421
1488  Topic20    1070.712036     지휘    1071.905029   5.6257  -3.3108
1634  Top

# 키워드 추출

In [36]:
topics = lda_model.print_topics(num_words=20) #topic 별 20개 keyword 보여줌 # 이 중 가중치가 0인것들 빼고 저장시킨다. 
for topic in topics:
    print(topic)

(0, '0.030*"지수" + 0.026*"업종" + 0.025*"거래" + 0.025*"오른" + 0.024*"상승" + 0.022*"하락" + 0.019*"강세" + 0.019*"포인트" + 0.018*"마감" + 0.018*"증시" + 0.018*"코스피" + 0.017*"코스닥" + 0.017*"종목" + 0.016*"시가총액" + 0.016*"유가" + 0.016*"매수" + 0.016*"기관" + 0.015*"기록" + 0.014*"상승세" + 0.014*"전날"')
(1, '0.036*"서비스" + 0.034*"사물인터넷" + 0.034*"지능" + 0.030*"통신" + 0.030*"스마트" + 0.024*"시스템" + 0.024*"제공" + 0.023*"기기" + 0.023*"플랫폼" + 0.023*"자동차" + 0.021*"방침" + 0.020*"차량" + 0.020*"정보" + 0.018*"빅데이터" + 0.017*"데이터" + 0.014*"전문" + 0.014*"기능" + 0.014*"인터넷" + 0.014*"네트워크" + 0.013*"센서"')
(2, '0.030*"우려" + 0.026*"노트" + 0.022*"가능성" + 0.019*"불확실" + 0.018*"상황" + 0.017*"정책" + 0.016*"금리" + 0.015*"부담" + 0.015*"경기" + 0.014*"주의" + 0.013*"기업" + 0.013*"부정" + 0.012*"기조" + 0.012*"침체" + 0.012*"미국" + 0.012*"요인" + 0.012*"작용" + 0.011*"리스크" + 0.011*"정치" + 0.011*"위축"')
(3, '0.129*"계약" + 0.113*"체결" + 0.079*"장비" + 0.069*"공급" + 0.066*"제조" + 0.060*"규모" + 0.060*"재료" + 0.057*"반도체" + 0.045*"매출" + 0.040*"변경" + 0.038*"기간" + 0.033*"사항" + 0.018*"답변" + 0.016*"

In [37]:
topics[0][1]

'0.030*"지수" + 0.026*"업종" + 0.025*"거래" + 0.025*"오른" + 0.024*"상승" + 0.022*"하락" + 0.019*"강세" + 0.019*"포인트" + 0.018*"마감" + 0.018*"증시" + 0.018*"코스피" + 0.017*"코스닥" + 0.017*"종목" + 0.016*"시가총액" + 0.016*"유가" + 0.016*"매수" + 0.016*"기관" + 0.015*"기록" + 0.014*"상승세" + 0.014*"전날"'

In [38]:
topic_0_1=topics[0][1].split('+')

In [39]:
topic_0_1

['0.030*"지수" ',
 ' 0.026*"업종" ',
 ' 0.025*"거래" ',
 ' 0.025*"오른" ',
 ' 0.024*"상승" ',
 ' 0.022*"하락" ',
 ' 0.019*"강세" ',
 ' 0.019*"포인트" ',
 ' 0.018*"마감" ',
 ' 0.018*"증시" ',
 ' 0.018*"코스피" ',
 ' 0.017*"코스닥" ',
 ' 0.017*"종목" ',
 ' 0.016*"시가총액" ',
 ' 0.016*"유가" ',
 ' 0.016*"매수" ',
 ' 0.016*"기관" ',
 ' 0.015*"기록" ',
 ' 0.014*"상승세" ',
 ' 0.014*"전날"']

In [40]:
float(topic_0_1[0].replace('*',' ').replace("\"","").split()[0])

0.03

In [41]:
topic_0_1[0].replace('*',' ').replace("\"","").split()

['0.030', '지수']

In [42]:
def make_keyword(data): #topic[0][1],topic[1],[1], . . . , topic[19][1] 이런식으로 넣음 
    topic_sep1=data.split('+')
    
    topic_keyword=[]
    topic_keyword_del=[]
    
    for i in range(20):
        topic_sep1[i]=topic_sep1[i].replace('*',' ').replace("\"","").split()
        #print(topic_sep1[i])
        
        if float(topic_sep1[i][0])>0: #가중치가 0보다 크면 keyword 에 저장 
            topic_keyword.append(topic_sep1[i][1]) 
            
        else:
            topic_keyword_del.append(topic_sep1[i][1]) #혹시 del된 단어들 보고싶다면 여기서 
            
        
    return topic_keyword

In [43]:
make_keyword(topics[0][1])

['지수',
 '업종',
 '거래',
 '오른',
 '상승',
 '하락',
 '강세',
 '포인트',
 '마감',
 '증시',
 '코스피',
 '코스닥',
 '종목',
 '시가총액',
 '유가',
 '매수',
 '기관',
 '기록',
 '상승세',
 '전날']

In [44]:
topic_keyword_all=[]

for i in range(20):
    topic_keyword_all.append(make_keyword(topics[i][1]))

topic_keyword_all   

[['지수',
  '업종',
  '거래',
  '오른',
  '상승',
  '하락',
  '강세',
  '포인트',
  '마감',
  '증시',
  '코스피',
  '코스닥',
  '종목',
  '시가총액',
  '유가',
  '매수',
  '기관',
  '기록',
  '상승세',
  '전날'],
 ['서비스',
  '사물인터넷',
  '지능',
  '통신',
  '스마트',
  '시스템',
  '제공',
  '기기',
  '플랫폼',
  '자동차',
  '방침',
  '차량',
  '정보',
  '빅데이터',
  '데이터',
  '전문',
  '기능',
  '인터넷',
  '네트워크',
  '센서'],
 ['우려',
  '노트',
  '가능성',
  '불확실',
  '상황',
  '정책',
  '금리',
  '부담',
  '경기',
  '주의',
  '기업',
  '부정',
  '기조',
  '침체',
  '미국',
  '요인',
  '작용',
  '리스크',
  '정치',
  '위축'],
 ['계약',
  '체결',
  '장비',
  '공급',
  '제조',
  '규모',
  '재료',
  '반도체',
  '매출',
  '변경',
  '기간',
  '사항',
  '답변',
  '대비',
  '전방',
  '공정',
  '수주',
  '테크',
  '국제무역',
  '중국'],
 ['산업',
  '기술',
  '위해',
  '기업',
  '분야',
  '반도체',
  '지원',
  '미래',
  '통해',
  '사업',
  '계획',
  '추진',
  '협력',
  '개발',
  '정부',
  '성과',
  '혁신',
  '구축',
  '적극',
  '전략'],
 ['프로그램',
  '과학',
  '표준',
  '신뢰',
  '기여',
  '합동',
  '근거',
  '과학기술',
  '규명',
  '미래창조과학부',
  '후속',
  '발굴',
  '수집',
  '계산',
  '제정',
  '항공우주',
  '포괄',
  '구단',
  '명목',
  '유연

In [45]:
#topic 0번 
topic_keyword_all[0]  

['지수',
 '업종',
 '거래',
 '오른',
 '상승',
 '하락',
 '강세',
 '포인트',
 '마감',
 '증시',
 '코스피',
 '코스닥',
 '종목',
 '시가총액',
 '유가',
 '매수',
 '기관',
 '기록',
 '상승세',
 '전날']

In [46]:
result=pd.DataFrame(topic_keyword_all)

In [47]:
result2=result.T

In [48]:
result

0      1    2    3     4      5      6     7    8        9      10   11  \
0     지수     업종   거래   오른    상승     하락     강세   포인트   마감       증시    코스피  코스닥   
1    서비스  사물인터넷   지능   통신   스마트    시스템     제공    기기  플랫폼      자동차     방침   차량   
2     우려     노트  가능성  불확실    상황     정책     금리    부담   경기       주의     기업   부정   
3     계약     체결   장비   공급    제조     규모     재료   반도체   매출       변경     기간   사항   
4     산업     기술   위해   기업    분야    반도체     지원    미래   통해       사업     계획   추진   
5   프로그램     과학   표준   신뢰    기여     합동     근거  과학기술   규명  미래창조과학부     후속   발굴   
6    일자리     특수   정기   개혁   필요성    최대한     행위    권리   제재       시사     포럼  정치권   
7     수출     정부   업종   조선    경제   구조조정    자동차    규제   소비       국산     정책   의존   
8     전망     실적   투자   증가    예상    반도체     대비    개선   이익       분석     영업   증권   
9     문제     때문   대해   지금   대통령     이유     대한    당시   과정       지난     생각   현실   
10    대체     단일   광학   광장  저장장치  전기자동차  하드디스크    지휘   주역      수상자     결실   복원   
11    현지     퀄컴   미국   행사    발굴     협회     구글   소비자   나선       시대  최고경영자   세계   
12   반도체     기업   투자   회사    인수     결정     설립   외국인   관련       화학     자금   규모   
13    지역     산업   시설   건설    예정     공장     규모   반도체  경기도       위치     여러   조성   
14    시장     제품   업계   생산   반도체   스마트폰     중국    최대   사업       세계     경쟁   공급   
15    수출     감소   수입   철강    증가     무역     통상    중국   선박       별로     산업  자동차   
16    사용     개발   기술   기존    적용    반도체     활용    장치   이용      차세대     최초   연구   
17    사장     총괄   경영   합병   텔레콤     회장    시너지   리더십   부문    최고경영자     조직   추구   
18    건강     사고   피해   이해   노동자     보건     발생    안전   사망       거부     인용   복지   
19   제조업     공식   동향   공업    소비     통계     설비    생산   차질       파업   서비스업   건설   

      12    13   14    15      16   17     18   19  
0     종목  시가총액   유가    매수      기관   기록    상승세   전날  
1     정보  빅데이터  데이터    전문      기능  인터넷   네트워크   센서  
2     기조    침체   미국    요인      작용  리스크     정치   위축  
3     답변    대비   전방    공정      수주   테크   국제무역   중국  
4     협력    개발   정부    성과      혁신   구축     적극   전략  
5     수집    계산   제정  항공우주      포괄   구단     명목  유연성  
6     가스   돌파구   거치    처벌      차관   장면     통제  원동력  
7     재정   선진국   항공    불황    우리나라   해양     수입   중국  
8     상승    지속   기록    유지      기준   가격     라며   평균  
9     가장    의미   상황    처음      시대   요구     가지   지적  
10   자외선  인사이트   재배    내일      본질   고수     상존   주석  
11    개국    관심   참가  전자기기  라스베이거스   공개     화두   연설  
12    보유    법인   최대    지난      중국   국내     미국   사업  
13    이전    계획   구성   부동산      선임   생활    관계자   전국  
14   관계자   메모리  글로벌    부품      지난   기술  디스플레이   전망  
15  석유화학   자원부   달러    주력      미국   관세    반도체   기간  
16    공정    효율   전력    제작      성능   구조     방식   설명  
17    사진    종이   체제    발행    조직개편   통합     참석   인수  
18    반복   반도체   조사    취재      수사   장소     순간   공장  
19    통신    장비  자동차   텍사스     스위스   산업     개월   경기

In [49]:
result2

0      1    2     3    4        5    6     7    8    9      10      11  \
0     지수    서비스   우려    계약   산업     프로그램  일자리    수출   전망   문제     대체      현지   
1     업종  사물인터넷   노트    체결   기술       과학   특수    정부   실적   때문     단일      퀄컴   
2     거래     지능  가능성    장비   위해       표준   정기    업종   투자   대해     광학      미국   
3     오른     통신  불확실    공급   기업       신뢰   개혁    조선   증가   지금     광장      행사   
4     상승    스마트   상황    제조   분야       기여  필요성    경제   예상  대통령   저장장치      발굴   
5     하락    시스템   정책    규모  반도체       합동  최대한  구조조정  반도체   이유  전기자동차      협회   
6     강세     제공   금리    재료   지원       근거   행위   자동차   대비   대한  하드디스크      구글   
7    포인트     기기   부담   반도체   미래     과학기술   권리    규제   개선   당시     지휘     소비자   
8     마감    플랫폼   경기    매출   통해       규명   제재    소비   이익   과정     주역      나선   
9     증시    자동차   주의    변경   사업  미래창조과학부   시사    국산   분석   지난    수상자      시대   
10   코스피     방침   기업    기간   계획       후속   포럼    정책   영업   생각     결실   최고경영자   
11   코스닥     차량   부정    사항   추진       발굴  정치권    의존   증권   현실     복원      세계   
12    종목     정보   기조    답변   협력       수집   가스    재정   상승   가장    자외선      개국   
13  시가총액   빅데이터   침체    대비   개발       계산  돌파구   선진국   지속   의미   인사이트      관심   
14    유가    데이터   미국    전방   정부       제정   거치    항공   기록   상황     재배      참가   
15    매수     전문   요인    공정   성과     항공우주   처벌    불황   유지   처음     내일    전자기기   
16    기관     기능   작용    수주   혁신       포괄   차관  우리나라   기준   시대     본질  라스베이거스   
17    기록    인터넷  리스크    테크   구축       구단   장면    해양   가격   요구     고수      공개   
18   상승세   네트워크   정치  국제무역   적극       명목   통제    수입   라며   가지     상존      화두   
19    전날     센서   위축    중국   전략      유연성  원동력    중국   평균   지적     주석      연설   

     12   13     14    15   16     17   18    19  
0   반도체   지역     시장    수출   사용     사장   건강   제조업  
1    기업   산업     제품    감소   개발     총괄   사고    공식  
2    투자   시설     업계    수입   기술     경영   피해    동향  
3    회사   건설     생산    철강   기존     합병   이해    공업  
4    인수   예정    반도체    증가   적용    텔레콤  노동자    소비  
5    결정   공장   스마트폰    무역  반도체     회장   보건    통계  
6    설립   규모     중국    통상   활용    시너지   발생    설비  
7   외국인  반도체     최대    중국   장치    리더십   안전    생산  
8    관련  경기도     사업    선박   이용     부문   사망    차질  
9    화학   위치     세계    별로  차세대  최고경영자   거부    파업  
10   자금   여러     경쟁    산업   최초     조직   인용  서비스업  
11   규모   조성     공급   자동차   연구     추구   복지    건설  
12   보유   이전    관계자  석유화학   공정     사진   반복    통신  
13   법인   계획    메모리   자원부   효율     종이  반도체    장비  
14   최대   구성    글로벌    달러   전력     체제   조사   자동차  
15   지난  부동산     부품    주력   제작     발행   취재   텍사스  
16   중국   선임     지난    미국   성능   조직개편   수사   스위스  
17   국내   생활     기술    관세   구조     통합   장소    산업  
18   미국  관계자  디스플레이   반도체   방식     참석   순간    개월  
19   사업   전국     전망    기간   설명     인수   공장    경기

In [50]:
# 엑셀 저장

result2.to_excel('C:\\Users\\user\\Desktop\\기타\\topic_keyword.xlsx')